## Computation of persistent homology with Ripserer

We will look at the Julia package `Ripserer` and see how it can be used to compute persistent (co)homology of a point cloud. Input to `ripserer(...)` can be a list of $n$-tuples representing points in $\mathbb{R}^n$. `Ripserer` will then perform persistent homology computation on the corresponding Vietoris-Rips complexes with increasing radii and return a list of `[birth, death)` intervals (and more).

We will be using Julia packages `LinearAlgebra`, `Plots`, `PersistenceDiagrams`, and, of course, `Ripserer`. Make sure you have these preinstalled.

In [1]:
# Let's load the packages.
using LinearAlgebra, Plots, Ripserer, PersistenceDiagrams

### A simple example with nonzero $H_2$

Let's start with a simple 6-point example in $\mathbb{R}^3$ - vertices of a non-regular octahedron. The position of vertices ensures that the Vietoris-Rips complex will have non-vanishing $H_1$ and $H_2$ at some level.

In [ ]:
# the vertices of our octahedron
octahedron = [(-1.0,0,0), (1.0,0,0), (0,1.0,0), (0,-1.0,0), (0,0,1.5), (0,0,-1.3)]
# and corresponding persistence intervals
diagram = ripserer(octahedron)
# draw the barcode diagram
# (and optionally change the coloring theme)
theme(:dark)
barcode(diagram)

In [ ]:
# Default Ripserer behaviour: compute cohomology up to H1 and use Z/2 coefficients. 
# Let's modify this.
diagram = ripserer(octahedron; dim_max = 2, modulus = 5, alg = :homology)
# The 'modulus = 5' keyword argument is equivalent to 'field = Mod{5}'. Field can also be set to rationals via 'field = Rational{Int64}'.
# The 'alg = ...' keyword argument can be ':cohomology' (default), ':homology' (slower) or ':involuted' (uses cohomology to find homology generators).
barcode(diagram)

### Extracting generating cycles

`Ripserer` also provides generating cycles of persistent homology groups. Let's extract them. 

In [ ]:
# Let's extract the most persistent 1-cycle.
most_persistent = diagram[2][end]
representative(most_persistent)

### Using custom filtrations

Ripserer also supports custom filtations. The function `Custom` will generate such a filtration (with Ripserer's internal data structure) from a dictionary with entries of the form `'abstract simplex' => 'level of filtration'`.

In [ ]:
# This is the example we had at the problem seesions (week 10, task 2).
K = Custom([(1,) => 0, (3,) => 0, (2,4) => 1, (1,4) => 2, (2,3) => 2, (3,4) => 3, (1,2) => 4, (1,2,4) => 5])
diagram_K = ripserer(K; field = Rational{Int64}, alg = :homology)
barcode(diagram_K) 

### Using Ripserer on sample data

`Ripserer` is mainly intended for point cloud data and corresponding Vietoris-Rips filtrations. Let's start by generating some planar point clouds as example test cases.

In [110]:
# A circular annulus. 
#
# initialize an empty 2-row matrix
annulus = Tuple{Float64, Float64}[] 
for _ in 1:600
    # a random point in the square [-1, 1] x [-1, 1]
    point = 2*rand(2) .- 1
    # check if this point is in an annulus
    if 0.75 <= norm(point) <= 1
        # and add it
        push!(annulus, Tuple(point))
    end
end

In [ ]:
# scatter plot the point cloud
scatter(annulus; aspect_ratio = 1, label = "")

In [ ]:
pers_annulus = ripserer(annulus; dim_max = 2)
barcode(pers_annulus)

In [ ]:
# The 'barcodes' in the barcode diagram (actually the intervals in the ripserer output) are ordered from the shortest one to the longest one. 
# Plotting the persistence diagram is even more direct.
plot(pers_annulus)

In [ ]:
# Another 2D example: two 'joined' circular annuli.
#
annulus2 = Tuple{Float64, Float64}[]  
for _ in 1:800
    # a random point in the square [-2, 2] x [-1, 1]
    point = [4; 2].*rand(2, 1) - [2; 1]
    # check if this point is in one of the two annuli
    if 0.7 <= norm(point - [0.85; 0]) <= 1 || 0.7 <= norm(point + [0.85; 0]) <= 1
        # and add it
        push!(annulus2, Tuple(point))
    end
end
# another scatter plot of the point cloud
scatter(annulus2; aspect_ratio = 1, label = "")

In [ ]:
# Let's actually compute homology this time. We'll use the :involuted algorithm as the actual :homology algorithm is slower.
pers_annulus2 = ripserer(annulus2; dim_max = 2, alg = :involuted)

In [ ]:
# We can also plot the barcode corresponding to H1 separately.
barcode(pers_annulus2[2])

In [ ]:
# There are two long-lived homology classes in H1. (Those correspond to the last two H1 persistence intervals.) Let's draw them.
scatter(annulus2; label = "data", aspect_ratio = 1)
first_class = pers_annulus2[2][end-1]
second_class = pers_annulus2[2][end]
# Loading the Ripserer package add additional functionality to (2D) plot! function - the call 'plot!(class, data)' will plot the homology class wrt. data.
plot!(first_class, annulus2; label = "1st H1 class")
plot!(second_class, annulus2; label = "2nd H1 class")

In [ ]:
# A 3D example: a hollow cube.
#
hollow_cube = Tuple{Float64, Float64, Float64}[]  
for _ in 1:800
    # a random point in the cube [-1, 1]x[-1, 1]x[-1, 1]
    point = 2*rand(3, 1) .- 1
    # check if this point is close enough to the boundary of the cube
    if 0.7 <= maximum(abs.(point)) <= 1
        # and add it
        push!(hollow_cube, Tuple(point))
    end
end
# another scatter plot of the point cloud
scatter(hollow_cube; aspect_ratio = 1, label = "")

In [ ]:
# Is this really a hollowed cube in this image? (I.e., is there a persistent enough 2-cycle in H2?)
pers_hollow_cube = ripserer(hollow_cube; dim_max = 2, threshold = 1)
# Let's check the barcode...
barcode(pers_hollow_cube)

In [ ]:
# Another 3D example: a 'wedge' of two 'thickened 2-spheres'.
#
two_spheres = Tuple{Float64, Float64, Float64}[]  
for _ in 1:1200
    # a random point in the box [-2, 2]x[-1, 1]x[-1, 1]
    point = [4, 2, 2].*rand(3, 1) - [2, 1, 1]
    # check if this point is within a thickened sphere around (1, 0, 0) or (-1, 0, 0)
    if 0.7 <= norm(point - [1, 0, 0]) <= 1 || 0.7 <= norm(point + [1, 0, 0]) <= 1
        # and add it
        push!(two_spheres, Tuple(point))
    end
end
# another scatter plot of the point cloud
scatter(two_spheres; aspect_ratio = 1, label = "")

In [ ]:
# How many '3D holes' do we have?
pers_two_spheres = ripserer(two_spheres; dim_max = 2, threshold = 1.5)
# Let's check the barcode...
barcode(pers_two_spheres[3])

In [ ]:
# A 4D example. A flat torus.
angles = LinRange(0, 2*pi, 21)[1:end-1]
torus = [(cos(ϕ), sin(ϕ), cos(θ), sin(θ)) for ϕ in angles for θ in angles]
# We only consider the Vietoris-Rips complex with ball radii at most 1 (threshold = 1) and we only keep the persisstence intervals longer than 0.5 (cutoff = 0.5).
pers_torus = ripserer(torus; dim_max = 2, threshold = 1, cutoff = 0.5, modulus = 3)
barcode(pers_torus)

In [ ]:
# An example in 6D. Do you know what this is?
sphere = Tuple{Float64, Float64, Float64}[] 
for _ in 1:1500
    # a random point in the box [-1, 1]x[-1, 1]x[-1, 1]
    point = 2*rand(3, 1) .- 1
    # check if this point is within a thickened sphere around (0, 0, 0)
    if 0.8 <= norm(point) <= 1
        # and add it
        push!(sphere, Tuple(point))
    end
end
whats_this = [(u^2, v^2, w^2, v*w, u*w, u*v) for (u, v, w) in sphere]

In [ ]:
# Let's try with Z/3 coefficients first.
pers_whats_this = ripserer(whats_this; dim_max = 2, modulus = 3)
barcode(pers_whats_this)

In [ ]:
# What about Z/2 coefficients?
pers_whats_this = ripserer(whats_this; dim_max = 2, modulus = 2)
barcode(pers_whats_this)